In [289]:
import influxdb_client, os, time
from influxdb_client import InfluxDBClient, Point, WritePrecision
from influxdb_client.client.write_api import SYNCHRONOUS
import pandas as pd
from tqdm import tqdm

from datetime import datetime, timedelta
import influxBackup as ib

import plotly.express as px
from IPython.display import display
import plotly.graph_objects as go
from IPython.display import Markdown

import plotly
from plotly.subplots import make_subplots
from PIL import Image

import io
import base64

In [290]:

client = ib.getInfuxClient()
plotly.offline.init_notebook_mode(connected=True)


In [291]:
markdown_string = f"""
# Health report <font size="4">{datetime.now().strftime("%Y-%m-%d %H:%M:%S")}</font>
"""
display(Markdown(markdown_string))


# Health report <font size="4">2023-12-06 15:56:17</font>


## User Information


In [292]:
start = datetime.today() - timedelta(days=365)
stop = datetime.today() + timedelta(days=1)
start_iso = start.isoformat("T") + "Z"
stop_iso = stop.isoformat("T") + "Z"
gender_response = ib.get(client, ["PersonalInfo"], ["gender"],start_iso, stop_iso)
gender = gender_response[0].records[0].values["_value"]
birthday_response = ib.get(client, ["PersonalInfo"], ["birthDate"],start_iso, stop_iso)
birthday = birthday_response[0].records[0].values["_value"]
age = int((datetime.today() - datetime.strptime(birthday, "%Y-%m-%d")).days / 365)
weight_response = ib.get(client, ["PersonalInfo"], ["weight"],start_iso, stop_iso)
weight = weight_response[0].records[0].values["_value"]/1000
height_response = ib.get(client, ["PersonalInfo"], ["height"],start_iso, stop_iso)
height = height_response[0].records[0].values["_value"]/100
# compute bmi
bmi = int(weight / (height * height))

markdown_string = f"""<font size="4">**Gender**: {gender}<br>**DOB**: {birthday}<br>**Age**: {age}<br>**Weight**: {weight} kg<br>**Height**: {height} m</font>"""

display(Markdown(markdown_string))



<font size="4">**Gender**: MALE<br>**DOB**: 1997-07-05<br>**Age**: 26<br>**Weight**: 63.999 kg<br>**Height**: 1.7 m</font>

## Weight

In [293]:

dfs = ib.populate_df(client, ["Weight"], ["weight"], start, stop)
weight_df = dfs[0]
weights = weight_df["weight"]/1000
heights = [height for i in range(len(weight_df))]
bmis = [weights[i]/(heights[i]*heights[i]) for i in range(len(weight_df))]

fig = make_subplots(rows=1, cols=2, subplot_titles=("BMI","Weight" ))
fig.add_trace(go.Scatter(x=weights, y=heights, mode="markers", marker=dict(color="black", size=5), showlegend=False,
                        text=bmis,
                        hovertemplate="Weight: %{x} kg<br>Height: %{y} m<br>BMI: %{text}<extra></extra>"
                         ), row=1, col=1)



img = Image.open("BMI_chart.png")

# Convert the PIL image to a data URI string
img_data = io.BytesIO()
img.save(img_data, format="PNG")
img_str = "data:image/png;base64," + base64.b64encode(img_data.getvalue()).decode()


# set axis range
fig.update_xaxes(range=[36, 120], row=1, col=1)
fig.update_yaxes(range=[1.4, 2], row=1, col=1)
fig.add_layout_image(
        dict(
            source=img_str,
            xref="x",
            yref="y",
            x=36,
            y=2,
            sizex=120 - 36,
            sizey=2-1.4,
            sizing="stretch",
            opacity=1,
            layer="below"),
        row=1, col=1
    
)


# add labels
fig.update_xaxes(title_text="weight (kg)", row=1, col=1)
fig.update_yaxes(title_text="height (m)", row=1, col=1)
# add title

# add legend to explain bmi categories
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="blue", size=5), name="Underweight"), row=1, col=1)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="green", size=5), name="Normal"), row=1, col=1)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="yellow", size=5), name="Overweight"), row=1, col=1)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="lightcoral", size=5), name="Moderately obese"), row=1, col=1)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="red", size=5), name="Severely obese"), row=1, col=1)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="darkred", size=5), name="Very severely obese"), row=1, col=1)
# move legend to below plot
fig.update_layout(legend=dict(
    orientation="h",
    yanchor="top",
    y=-0.15,
    xanchor="right",
    x=0.9
))

# plot weight over time
fig.add_trace(go.Scatter(x=weight_df.index, y=weight_df["weight"]/1000, mode="lines+markers", marker=dict(color="black", size=5), showlegend=False
                         # only show marker values on hover
                            , hovertemplate = "Weight: %{y} kg<br>Date: %{x}<extra></extra>"
                         ), row=1, col=2)
# set axis labels
fig.update_xaxes(title_text="date", row=1, col=2)
fig.update_yaxes(title_text="weight (kg)", row=1, col=2)
# remove padding around plot
margin = 80
fig.update_layout(margin=dict(l=margin, r=margin, b=margin, t=margin))
fig.update_layout(title_text="BMI: " + str(round(bmi, 1)))
# set aspect ratio
fig.update_layout(autosize=False, width=900, height=500)
display(fig)

In [294]:

markdown_string = f"""
Your BMI is **{bmi}** which is considered 
"""
if bmi < 18.5:
    markdown_string += "**underweight**"
elif bmi < 25:
    markdown_string += "**normal**"
elif bmi < 30:
    markdown_string += "**overweight**"
else:
    markdown_string += "**obese**"
    
display(Markdown(markdown_string))


Your BMI is **22** which is considered 
**normal**

## Heart rate metrics

In [295]:

markdown_string = f"Below is your resting hear rate from {start.strftime('%Y-%m-%d')} to {stop.strftime('%Y-%m-%d')}\n\n"
display(Markdown(markdown_string))

Below is your resting hear rate from 2022-12-06 to 2023-12-07



In [296]:
dfs = ib.populate_df(client, ["HeartRateMetrics","RealTimeHeartRate"], ["restingHeartRate", "heartRateValue"], start, stop)

fig = go.Figure()
for df in dfs:
    fig.add_trace(go.Scatter(x=df.index, y=df[df.columns[0]], mode="lines", name=df.columns[0]))
fig.update_layout(autosize=False, width=900, height=500)
display(fig)






In [297]:
# compute the average resting heart rate
average_heart_rate = 0
# compute max heart rate
max_heart_rate = 0
# compute min heart rate
for df in dfs:
    # print name of the dataframe
    if df.columns[0] == "restingHeartRate":
        average_heart_rate = round(df["restingHeartRate"].mean(),2)
    elif df.columns[0] == "heartRateValue":
        max_heart_rate = round(df["heartRateValue"].max(),2)
        min_heart_rate = round(df["heartRateValue"].min(),2)

In [298]:

nb_months = (stop.year - start.year) * 12 + (stop.month - start.month)
markdown_string = f"Your average resting heart rate in the last {nb_months} months was **{average_heart_rate}** bpm."
if average_heart_rate < 60:
    markdown_string += " This is below the target resting heart rate of 60 bpm. Congratulations!"
else:
    markdown_string += " This is above the target resting heart rate of 60 bpm!"

# Print or use the formatted Markdown string
display(Markdown(markdown_string))

theoretical_max_heart_rate = 220 - 26
markdown_string = f"Your max heart rate in the last {nb_months} months was **{max_heart_rate}** bpm, which is {round(max_heart_rate/190*100,2)}% of your theoretical max heart rate of {theoretical_max_heart_rate} bpm.\n\n"
if max_heart_rate > theoretical_max_heart_rate:
    markdown_string += "This is above the theoretical max heart rate of 190 bpm. You should consult a doctor."
elif max_heart_rate < theoretical_max_heart_rate * 0.9:
    markdown_string += "This is well below the theoretical max heart rate of {theoretical_max_heart_rate} bpm. Should you be doing more high intensity workouts?"
display(Markdown(markdown_string))


Your average resting heart rate in the last 12 months was **47.84** bpm. This is below the target resting heart rate of 60 bpm. Congratulations!

Your max heart rate in the last 12 months was **183** bpm, which is 96.32% of your theoretical max heart rate of 194 bpm.



## Blood pressure 

In [299]:
dfs = ib.populate_df(client, ["BloodPressure"], ["diastolic", "systolic"], start, stop)

# get all the diasystolic and systolic values
for df in dfs:
    if df.columns[0] == "diastolic":
        diastolic = df["diastolic"]
    elif df.columns[0] == "systolic":
        systolic = df["systolic"]
diastolic_colours = []
systolic_colours = []
for i in range(len(diastolic)):
    if diastolic.iloc[i] < 80:
        diastolic_colours.append("green")
    elif diastolic.iloc[i] < 90:
        diastolic_colours.append("orange")
    else:
        diastolic_colours.append("red")
for i in range(len(systolic)):
    if systolic.iloc[i] < 120:
        systolic_colours.append("green")
    elif systolic.iloc[i] < 130:
        systolic_colours.append("orange")
    else:
        systolic_colours.append("red")
fig = make_subplots(rows=1, cols=2, subplot_titles=("Blood pressure over time", "Blood pressure zones"))
fig.add_trace(go.Scatter(x=diastolic.index, y=diastolic, mode="markers", marker=dict(color=diastolic_colours, size=5), name="diastolic",showlegend=False,
                         hovertemplate="Diastolic: %{y} mmHg<br>Date: %{x}<extra></extra>"), row=1, col=1)
fig.add_trace(go.Scatter(x=systolic.index, y=systolic, mode="markers", marker=dict(color=systolic_colours, size=5), name="systolic",showlegend=False,
                        hovertemplate="Systolic: %{y} mmHg<br>Date: %{x}<extra></extra>"), row=1, col=1)
# draw a vertical line between the systolic and diastolic values # set the color to be green if the values are within the normal range, orange if they are in the warning range, and red if they are in the danger range
for i in range(len(diastolic)):
    diastolic_value = diastolic.iloc[i]
    systolic_value = systolic.iloc[i]
    if diastolic_value < 80 and systolic_value < 120:
        colour = "green"
    elif diastolic_value < 90 and systolic_value < 130:
        colour = "orange"
    else:
        colour = "red"
    # width should be 10
    fig.add_shape(type="line", x0=diastolic.index[i], y0=diastolic_value, x1=systolic.index[i], y1=systolic_value, line=dict(color=colour, width=5), opacity=0.5, row=1, col=1)
#set range
fig.update_yaxes(range=[40, 140],row=1, col=1)
fig.update_xaxes(range=[min(diastolic.index) - timedelta(days=1), max(diastolic.index) + timedelta(days=1)],row=1, col=1)
# add labels
fig.update_xaxes(title_text="date", row=1, col=1)
fig.update_yaxes(title_text="blood pressure (mmHg)", row=1, col=1)
######

systolic_time_stamps = []
for i in range(len(diastolic)):
    systolic_time_stamps.append(diastolic.index[i].strftime("%Y-%m-%d %H:%M:%S"))
colors = ["#3498db", "#1FC253", "#ff9800", "#e74c3c"]

# create a box around the normal range
fig.add_shape(type="rect",
    x0=0, y0=0, x1=100, y1=200,
    line=dict(color=colors[3]),#red
    fillcolor=colors[3],
    opacity=1,
    layer="below",
    row=1, col=2
)
fig.add_shape(type="rect",
    x0=0, y0=0, x1=90, y1=140,
    line=dict(color=colors[2]),#orange
    fillcolor=colors[2],
    opacity=1,
    layer="below",
    row=1, col=2
)
fig.add_shape(type="rect",
    x0=0, y0=0, x1=80, y1=120,
    line=dict(color=colors[1]),#green
    fillcolor=colors[1],
    opacity=1,
    layer="below",
    row=1, col=2
)
fig.add_shape(type="rect",
    x0=0, y0=0, x1=60, y1=90,
    line=dict(color=colors[0]),#blue
    fillcolor=colors[0],
    opacity=1,
    layer="below",
    row=1, col=2
)
# plot the systolic and diastolic data add date_time as marker text. marker color is black, 0.5 thinkness
fig.add_trace(go.Scatter(x=diastolic, y=systolic, mode="markers", marker=dict(color="black", size=5), text=systolic_time_stamps,showlegend=False,
                        hovertemplate = "Diastolic: %{x} mmHg<br>Systolic: %{y} mmHg<br>Date: %{text}<extra></extra>"), row=1, col=2)

# set axis range
fig.update_xaxes(range=[0, 100],dtick=20,showgrid=False,title_text="diastolic pressure (mmHg)", row=1, col=2)
fig.update_yaxes(range=[0, 200],dtick=20,showgrid=False,title_text="systolic pressure (mmHg)", row=1, col=2)

# add legend to explain bmi categories
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="blue", size=5), name="Hypotension"), row=1, col=2)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="green", size=5), name="Normal"), row=1, col=2)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="yellow", size=5), name="Prehypertension"), row=1, col=2)
fig.add_trace(go.Scatter(x=[0], y=[0], mode="markers", marker=dict(color="lightcoral", size=5), name="Hypertension"), row=1, col=2)


# move legend to below plot
fig.update_layout(legend=dict(
    orientation="h",
    yanchor="top",
    y=-0.15,
    xanchor="right",
    x=1.05
))
# add slider to select date range
fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                        label="1m",
                        step="month",
                        stepmode="backward"),
                dict(count=3,
                        label="3m",
                        step="month",
                        stepmode="backward")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)


# remove legend
# fig.update_layout(showlegend=False)
fig.update_layout(autosize=False, width=900, height=500)
display(fig)



In [300]:
!jupyter nbconvert --to html --no-input --no-prompt report.ipynb
# open report.html
import webbrowser
webbrowser.open('report.html')

[NbConvertApp] Converting notebook report.ipynb to html
[NbConvertApp] Writing 3729947 bytes to report.html


True